In [0]:
!wget https://github.com/jbrownlee/Datasets/releases/download/Flickr8k/Flickr8k_text.zip

In [0]:
"""

===============================================================
Prepared By:

    1. Ahmed El-Sayed Hamdan - 191035
    2. Mohamed Ahmed Elkhateeb - 191017
    3. Moaaz Youssef Ghonaimy - 191036
    4. Maryam Akram Elghalban - 191084
===============================================================

Documenation for the work done:
------------------------------------------------
1.	Read the dataset using spark
    a.	 using databricks.com by creating a cluster and loading the data directly
    b.	Check the number of partitions for each part of data
    c.	Repartition the data into 2 partitions because the cluster has one node 2 cores
    d.	Store the data as parquet
    e.	Reload the data again but from parquet files which save a lot of time
    i.	JSON files take about 16.87 minutes
    ii.	Parquet files take about 4.76 seconds

2.	Exploratory data analysis (EDA)
    a.	Print Schema to check the available columns 
    b.	Get most important columns (paper_id, title, abstract, body_text, back_matter)
    c.	Add “source” column and set the value with “comm, uncomm, bio”
    d.	Check about null and empty for all of these columns and this is the result
        •	null titles: 0 
        •	empty titles: 617
        •	null abstracts: 0
        •	abstracts has less than 100 char: 1624 
        •	abstracts has less than 100 char and not empty: 107
        •	null body_text: 0
        •	body_text has less than 10000 char: 1188
        •	body_text has less than 10000 char and not empty: 1188
        •	null back_matter: 0
        •	back_matter has less than 100 char: 3776
        •	back_matter has less than 100 char and not empty: 974
    e.	check about duplicate title and there are about 500 duplicate titles
    f.	check about language and there are about 100 documents non English (we filter step by step so these 5 after removing null duplicates and short body_text) using langdetect library

3.	Preparation and Cleaning the data
    a.	drop null and empty and short body text records
    b.	drop duplicate titles
    c.	keep only English document

4.	Preprocessing
    a.	Remove punctuations
    b.	Remove stop words
    c.	Remove custom stop words
    d.	convert text to lower case

5.	Vectorization 
    We use TF-IDF. 
    Here we try without using the feature_num parameters then it produce about 250k features, but unfortunately when apply PCA, it limited to only 16K features, so we limit the features num to 16K but then PCA has out of memery exception so then we decrease the features_num again and again with a lot of values (50000,10000,5000,1000,500)

6.	Clustering
    a.	Use Kmeans
    b.	Use PCA to reduce dimensions 

7.	Recommender system
    Unfortunately we didn’t start on this part

"""

In [0]:
# Configure Paths for the json files in databricks
comm_use_subset_path = "/databricks-datasets/COVID/CORD-19/2020-03-13/comm_use_subset/comm_use_subset/"
noncomm_use_subset_path = "/databricks-datasets/COVID/CORD-19/2020-03-13/noncomm_use_subset/noncomm_use_subset/"
biorxiv_medrxiv_path = "/databricks-datasets/COVID/CORD-19/2020-03-13/biorxiv_medrxiv/biorxiv_medrxiv/"
json_schema_path = "/databricks-datasets/COVID/CORD-19/2020-03-13/json_schema.txt"

In [0]:
# start loading the files
comm_use_subset = spark.read.option("multiLine", True).json(comm_use_subset_path)
noncomm_use_subset = spark.read.option("multiLine", True).json(noncomm_use_subset_path)
biorxiv_medrxiv = spark.read.option("multiLine", True).json(biorxiv_medrxiv_path)
json_schema_path = spark.read.option("multiLine", True).json(json_schema_path)

In [0]:
# Get number of partitions for each group of files
comm_use_subset.rdd.getNumPartitions()
noncomm_use_subset.rdd.getNumPartitions()
biorxiv_medrxiv.rdd.getNumPartitions()

In [0]:
#Configure Parquet Paths to be used to store the files and load later
comm_use_subset_pq_path = "/tmp/parquet/comm_use_subset.parquet"
noncomm_use_subset_pq_path = "/tmp/parquet/noncomm_use_subset.parquet"
biorxiv_medrxiv_pq_path = "/tmp/parquet/biorxiv_medrxiv/biorxiv_medrxiv.parquet"

In [0]:
# Write out in Pqarquet format in 2 partitions
# Note, this cluster has 2 nodes
comm_use_subset.repartition(2).write.format("parquet").mode("overwrite").save(comm_use_subset_pq_path)
noncomm_use_subset.repartition(2).write.format("parquet").mode("overwrite").save(noncomm_use_subset_pq_path)
biorxiv_medrxiv.repartition(2).write.format("parquet").mode("overwrite").save(biorxiv_medrxiv_pq_path)

In [0]:
comm_use_subset = spark.read.format("parquet").load(comm_use_subset_pq_path)
noncomm_use_subset = spark.read.format("parquet").load(noncomm_use_subset_pq_path)
biorxiv_medrxiv = spark.read.format("parquet").load(biorxiv_medrxiv_pq_path)

In [0]:
comm_use_subset.printSchema()

root
-- abstract: array (nullable = true)
 |-- element: struct (containsNull = true)
 | |-- cite_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- ref_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- section: string (nullable = true)
 | |-- text: string (nullable = true)
-- back_matter: array (nullable = true)
 |-- element: struct (containsNull = true)
 | |-- cite_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- ref_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- section: string (nullable = true)
 | |-- text: string (nullable = true)
-- bib_entries: struct (nullable = true)
 |-- BIBREF0: struct (nullable = true)
 | |-- authors: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- first: string (nullable = true)
 | | | |-- last: string (nullable = true)
 | | | |-- middle: array (nullable = true)
 | | | | |-- element: string (containsNull = true)
 | | | |-- suffix: string (nullable = true)
 | |-- issn: string (nullable = true)
 | |-- other_ids: struct (nullable = true)
 | | |-- DOI: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMCID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | |-- pages: string (nullable = true)
 | |-- ref_id: string (nullable = true)
 | |-- title: string (nullable = true)
 | |-- venue: string (nullable = true)
 | |-- volume: string (nullable = true)
 | |-- year: long (nullable = true)
 |-- BIBREF1: struct (nullable = true)
 | |-- authors: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- first: string (nullable = true)
 | | | |-- last: string (nullable = true)
 | | | |-- middle: array (nullable = true)
 | | | | |-- element: string (containsNull = true)
 | | | |-- suffix: string (nullable = true)
 | |-- issn: string (nullable = true)
 | |-- other_ids: struct (nullable = true)
 | | |-- DOI: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMCID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- arXiv: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | |-- pages: string (nullable = true)
 | |-- ref_id: string (nullable = true)
 | |-- title: string (nullable = true)
 | |-- venue: string (nullable = true)
 | |-- volume: string (nullable = true)
 | |-- year: long (nullable = true)
 |-- BIBREF10: struct (nullable = true)
 | |-- authors: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- first: string (nullable = true)
 | | | |-- last: string (nullable = true)
 | | | |-- middle: array (nullable = true)
 | | | | |-- element: string (containsNull = true)
 | | | |-- suffix: string (nullable = true)
 | |-- issn: string (nullable = true)
 | |-- other_ids: struct (nullable = true)
 | | |-- DOI: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMCID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMID: array (nullable = true)
 | | | |-- element: st

In [0]:
noncomm_use_subset.printSchema()

root
-- abstract: array (nullable = true)
 |-- element: struct (containsNull = true)
 | |-- cite_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- ref_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- section: string (nullable = true)
 | |-- text: string (nullable = true)
-- back_matter: array (nullable = true)
 |-- element: struct (containsNull = true)
 | |-- cite_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- ref_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- section: string (nullable = true)
 | |-- text: string (nullable = true)
-- bib_entries: struct (nullable = true)
 |-- BIBREF0: struct (nullable = true)
 | |-- authors: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- first: string (nullable = true)
 | | | |-- last: string (nullable = true)
 | | | |-- middle: array (nullable = true)
 | | | | |-- element: string (containsNull = true)
 | | | |-- suffix: string (nullable = true)
 | |-- issn: string (nullable = true)
 | |-- other_ids: struct (nullable = true)
 | | |-- DOI: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | |-- pages: string (nullable = true)
 | |-- ref_id: string (nullable = true)
 | |-- title: string (nullable = true)
 | |-- venue: string (nullable = true)
 | |-- volume: string (nullable = true)
 | |-- year: long (nullable = true)
 |-- BIBREF1: struct (nullable = true)
 | |-- authors: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- first: string (nullable = true)
 | | | |-- last: string (nullable = true)
 | | | |-- middle: array (nullable = true)
 | | | | |-- element: string (containsNull = true)
 | | | |-- suffix: string (nullable = true)
 | |-- issn: string (nullable = true)
 | |-- other_ids: struct (nullable = true)
 | | |-- DOI: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | |-- pages: string (nullable = true)
 | |-- ref_id: string (nullable = true)
 | |-- title: string (nullable = true)
 | |-- venue: string (nullable = true)
 | |-- volume: string (nullable = true)
 | |-- year: long (nullable = true)
 |-- BIBREF10: struct (nullable = true)
 | |-- authors: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- first: string (nullable = true)
 | | | |-- last: string (nullable = true)
 | | | |-- middle: array (nullable = true)
 | | | | |-- element: string (containsNull = true)
 | | | |-- suffix: string (nullable = true)
 | |-- issn: string (nullable = true)
 | |-- other_ids: struct (nullable = true)
 | | |-- DOI: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- arXiv: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | |-- pages: string (nullable = true)
 | |-- ref_id: string (nullable = true)
 | |-- title: string (nullable = true)
 | |-- venue: string (nullable = true)
 | |-- volume: string (nullable = true)
 | |-- year: long (nullable = true)
 |-- BI

In [0]:
biorxiv_medrxiv.printSchema()

root
-- abstract: array (nullable = true)
 |-- element: struct (containsNull = true)
 | |-- cite_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- ref_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- section: string (nullable = true)
 | |-- text: string (nullable = true)
-- back_matter: array (nullable = true)
 |-- element: struct (containsNull = true)
 | |-- cite_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- ref_spans: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- end: long (nullable = true)
 | | | |-- ref_id: string (nullable = true)
 | | | |-- start: long (nullable = true)
 | | | |-- text: string (nullable = true)
 | |-- section: string (nullable = true)
 | |-- text: string (nullable = true)
-- bib_entries: struct (nullable = true)
 |-- BIBREF0: struct (nullable = true)
 | |-- authors: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- first: string (nullable = true)
 | | | |-- last: string (nullable = true)
 | | | |-- middle: array (nullable = true)
 | | | | |-- element: string (containsNull = true)
 | | | |-- suffix: string (nullable = true)
 | |-- issn: string (nullable = true)
 | |-- other_ids: struct (nullable = true)
 | | |-- DOI: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | |-- pages: string (nullable = true)
 | |-- ref_id: string (nullable = true)
 | |-- title: string (nullable = true)
 | |-- venue: string (nullable = true)
 | |-- volume: string (nullable = true)
 | |-- year: long (nullable = true)
 |-- BIBREF1: struct (nullable = true)
 | |-- authors: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- first: string (nullable = true)
 | | | |-- last: string (nullable = true)
 | | | |-- middle: array (nullable = true)
 | | | | |-- element: string (containsNull = true)
 | | | |-- suffix: string (nullable = true)
 | |-- issn: string (nullable = true)
 | |-- other_ids: struct (nullable = true)
 | | |-- DOI: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMCID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- arXiv: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | |-- pages: string (nullable = true)
 | |-- ref_id: string (nullable = true)
 | |-- title: string (nullable = true)
 | |-- venue: string (nullable = true)
 | |-- volume: string (nullable = true)
 | |-- year: long (nullable = true)
 |-- BIBREF10: struct (nullable = true)
 | |-- authors: array (nullable = true)
 | | |-- element: struct (containsNull = true)
 | | | |-- first: string (nullable = true)
 | | | |-- last: string (nullable = true)
 | | | |-- middle: array (nullable = true)
 | | | | |-- element: string (containsNull = true)
 | | | |-- suffix: string (nullable = true)
 | |-- issn: string (nullable = true)
 | |-- other_ids: struct (nullable = true)
 | | |-- DOI: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMCID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- PMID: array (nullable = true)
 | | | |-- element: string (containsNull = true)
 | | |-- arXiv: array (nullable = true)
 | | | |-- element: st

In [0]:
display(comm_use_subset)

abstract back_matter bib_entries body_text metadata paper_id ref_entries List(List(List(), List(), Abstract, After Edward Jenner established human vaccination over 200 years ago, attenuated poxviruses became key players to contain the deadliest virus of its own family: Variola virus (VARV), the causative agent of smallpox. Cowpox virus (CPXV) and horsepox virus (HSPV) were extensively used to this end, passaged in cattle and humans until the appearance of vaccinia virus (VACV), which was used in the final campaigns aimed to eradicate the disease, an endeavor that was accomplished by the World Health Organization (WHO) in 1980. Ever since, naturally evolved strains used for vaccination were introduced into research laboratories where VACV and other poxviruses with improved safety profiles were generated. Recombinant DNA technology along with the DNA genome features of this virus family allowed the generation of vaccines against heterologous diseases, and the specific insertion and deletion of poxvirus genes generated an even broader spectrum of modified viruses with new properties that increase their immunogenicity and safety profile as vaccine vectors. In this review, we highlight the evolution of poxvirus vaccines, from first generation to the current status, pointing out how different vaccines have emerged and approaches that are being followed up in the development of more rational vaccines against a wide range of diseases.)) List(List(List(), List(), Acknowledgements, The experiment performed in the laboratory of M. Esteban was funded by research grants from Spain, EU 7th Framework Program and by the Bill and Melinda Gates Foundation. We thank all members of the lab for their continuous support.), List(List(), List(), Conflict of Interest, The authors declare no conflict of interest.)) List(List(List(List(D, Hopkins, List(R), )), , List(null, null, null), , b0, The Greatest Killer: Smallpox in History, with a New Introduction, , , 2002), List(List(List(J, Parrino, List(), ), List(B, Graham, List(S), )), , List(null, null, null, null), 1320--1326, b1, Smallpox vaccines: Past, present, and future, J. Allergy Clin. Immunol, 118, 2006), List(List(List(E, Nakano, List(), ), List(D, Panicali, List(), ), List(E, Paoletti, List(), )), , List(null, null, null, null), 1593--1596, b10, Molecular genetics of vaccinia virus: Demonstration of marker rescue, Proc. Natl. Acad. Sci, 79, 1982), List(List(List(J, Weger-Lucarelli, List(), ), List(H, Chu, List(), ), List(M, Aliota, List(T), ), List(C, Partidos, List(D), ), List(J, Osorio, List(E), )), , List(null, null, null, null), , b100, A novel MVA vectored Chikungunya virus vaccine elicits protective immunity in mice, PLOS Negl. Trop. Dis, , 2014), List(List(List(P, Van Den Doel, List(), ), List(A, Volz, List(), ), List(J, Roose, List(M), ), List(V, Sewbalaksing, List(D), ), List(G, Pijlman, List(P), ), List(I, Van Middelkoop, List(), ), List(V, Duiverman, List(), ), List(E, Van De Wetering, List(), ), List(G, Sutter, List(), ), List(A, Osterhaus, List(D), )), , List(null, null), , b101, Recombinant modified vaccinia virus Ankara expressing glycoprotein E2 of Chikungunya virus protects AG129 mice against lethal challenge, PLOS Negl. Trop. Dis, 8, 2014), List(List(List(R, Men, List(), ), List(L, Wyatt, List(), ), List(I, Tokimatsu, List(), ), List(S, Arakaki, List(), ), List(G, Shameem, List(), ), List(R, Elkins, List(), ), List(R, Chanock, List(), ), List(B, Moss, List(), ), List(C, Lai, List(J), )), , List(null, null), 3113--3122, b102, Immunization of rhesus monkeys with a recombinant of modified vaccinia virus Ankara expressing a truncated envelope glycoprotein of dengue type 2 virus induced resistance to dengue type 2 virus challenge, , 18, 2000), List(List(List(B, Quinan, List(R), ), List(I, Flesch, List(E), ), List(T, Pinho, List(M), ), List(F, Coelho, List(M), ), List(D, Tscharke, List(C), ), List(F, Da Fonseca, List(G), )), , List(null, null), 2972--2979, b103, An intact signal pe

In [0]:
display(comm_use_subset.select('abstract.text'))

text List(After Edward Jenner established human vaccination over 200 years ago, attenuated poxviruses became key players to contain the deadliest virus of its own family: Variola virus (VARV), the causative agent of smallpox. Cowpox virus (CPXV) and horsepox virus (HSPV) were extensively used to this end, passaged in cattle and humans until the appearance of vaccinia virus (VACV), which was used in the final campaigns aimed to eradicate the disease, an endeavor that was accomplished by the World Health Organization (WHO) in 1980. Ever since, naturally evolved strains used for vaccination were introduced into research laboratories where VACV and other poxviruses with improved safety profiles were generated. Recombinant DNA technology along with the DNA genome features of this virus family allowed the generation of vaccines against heterologous diseases, and the specific insertion and deletion of poxvirus genes generated an even broader spectrum of modified viruses with new properties that increase their immunogenicity and safety profile as vaccine vectors. In this review, we highlight the evolution of poxvirus vaccines, from first generation to the current status, pointing out how different vaccines have emerged and approaches that are being followed up in the development of more rational vaccines against a wide range of diseases.) List(which permits unrestricted use, distribution, and reproduction in any medium, provided you give appropriate credit to the original author(s) and the source, provide a link to the Creative Commons license, and indicate if changes were made., Oral communications Oral communications: Physiotherapists, Romain Lachal (speaker) Réanimation médicale, Hôpital de la Croix-Rousse,) List(Herpes simplex virus (HSV) type 1 and 2 are old viruses, with a history of evolution shared with humans. Thus, it is generally well-adapted viruses, infecting many of us without doing much harm, and with the capacity to hide in our neurons for life. In rare situations, however, the primary infection becomes generalized or involves the brain., Normally, the primary HSV infection is asymptomatic, and a crucial element in the early restriction of virus replication and thus avoidance of symptoms from the infection is the concerted action of different arms of the innate immune response. An early and light struggle inhibiting some HSV replication will spare the host from the real war against huge amounts of virus later in infection. As far as such a war will jeopardize the life of the host, it will be in both interests, including the virus, to settle the conflict amicably. Some important weapons of the unspecific defence and the early strikes and beginning battle during the first days of a HSV infection are discussed in this review., Generally, macrophages are orchestrating a multitude of anti-herpetic actions during the first hours of the attack. In a first wave of responses, cytokines, primarily type I interferons (IFN) and tumour necrosis factor are produced and exert a direct antiviral effect and activate the macrophages themselves. In the next wave, interleukin (IL)-12 together with the above and other cytokines induce production of IFN-γ in mainly NK cells. Many positive feed-back mechanisms and synergistic interactions intensify these systems and give rise to heavy antiviral weapons such as reactive oxygen species and nitric oxide. This results in the generation of an alliance against the viral enemy., However, these heavy weapons have to be controlled to avoid too much harm to the host. By IL-4 and others, these reactions are hampered, but they are still allowed in foci of HSV replication, thus focusing the activity to only relevant sites. So, no hero does it alone. Rather, an alliance of cytokines, macrophages and other cells seems to play a central role. Implications of this for future treatment modalities are shortly considered.) List(Critical Care 2016, 20(Suppl 2):P001, Introduction: A hallmark of sepsis is early on

In [0]:
noncomm_use_subset.show(5)

+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
 abstract| back_matter| bib_entries| body_text| metadata| paper_id| ref_entries|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
[[[], [], Abstrac...|[[[], [], acknowl...|[[[[Università, M...|[[[], [], , Nel p...|[[[[,,], , E, Tor...|ce6717ad3bb0da860...|[[, La sicurezza ...|
 []| []|[[[[V, Uversky, [...|[[[], [], , disor...|[[[[University of...|8fec2036fb2e98cbb...|[[, Intrinsic dis...|
 []|[[[], [], Acknowl...|[[[[J, Staats, [J...|[[[[212, BIBREF0,...|[[[[Zhejiang Univ...|43aeebc83e7567343...|[[, Global epidem...|
 []|[[[], [], annex, ...|[[[], , [,], , b0...|[[[], [], , Sacch...|[[], Research Com...|25a10dcacb257ac92...|[[, THE PROBIOTIC...|
 []| []|[[[[L, Ackermann,...|[[[], [], Introdu...|[[[[AbbVie, Inc, ...|0e18097a83b2801c4...|[[, corneaSpecies...|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
only showing top 5 rows

In [0]:
biorxiv_medrxiv.show(5)

+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
 abstract| back_matter| bib_entries| body_text| metadata| paper_id| ref_entries|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
[[[], [], Abstrac...| []|[[[[Y, Benjamini,...|[[[[176, BIBREF11...|[[[[University of...|26cb6703ca72bf978...|[[, ChRO-seq reve...|
[[[], [], Abstrac...|[[[], [], acknowl...|[[[[J, Adam, [], ...|[[[[163, BIBREF9,...|[[[[The Universit...|41d412415c46baf70...|[[, Amphiphysin d...|
[[[[1478, BIBREF1...|[[[[78, BIBREF50,...|[, [[[B, Degnan, ...|[[[[287,, 258, (G...|[[[[University of...|90e28ff462882ca7a...|[[, ). Moreover, ...|
[[[], [], Abstrac...| []|[[[[A, Hodgkin, [...|[[[], [], , ABSTR...|[[[[City College ...|e7c3ec3dcb3469ee4...|[[, (reproduced f...|
[[[], [], Abstrac...|[[[], [], Acknowl...|[[[[A, Minchinton...|[[[], [], , signi...|[[[[The Universit...|fcb76f0907f67a850...|[[, (a) Schematic...|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
only showing top 5 rows

In [0]:
from pyspark.sql.functions import col, lit, concat_ws, explode

# select columns which have text like title, abstract, body and backmatter
# select author object to make some processing later
# select paperid
comm_use_subset_selected = comm_use_subset.select(
            col("metadata.title").alias("title"),
            col("abstract.text").alias("abstract_arr"),
            col("body_text.text").alias("body_text_arr"),
            col("back_matter.text").alias("back_matter_arr"),
          #  col("metadata.authors").alias("authors_arr"),
            "paper_id")

# concatenate the paragraphs in one text for abstartc, body_text and back_matter
comm_use_subset_selected = comm_use_subset_selected.withColumn('abstract', concat_ws(' ', 'abstract_arr'))
comm_use_subset_selected = comm_use_subset_selected.withColumn('body_text', concat_ws(' ', 'body_text_arr'))
comm_use_subset_selected = comm_use_subset_selected.withColumn('back_matter', concat_ws(' ', 'back_matter_arr'))

# add column for source dataset
comm_use_subset_selected = comm_use_subset_selected.withColumn("source",lit("comm_use_subset"))

# drop unneeded columns 
comm_use_subset_selected = comm_use_subset_selected.drop("abstract_arr","body_text_arr","back_matter_arr")

comm_use_subset_selected.printSchema()

root
-- title: string (nullable = true)
-- paper_id: string (nullable = true)
-- abstract: string (nullable = false)
-- body_text: string (nullable = false)
-- back_matter: string (nullable = false)
-- source: string (nullable = false)

In [0]:
# select columns which have text like title, abstract, body and backmatter
# select author object to make some processing later
# select paperid
noncomm_use_subset_selected = noncomm_use_subset.select(
            col("metadata.title").alias("title"),
            col("abstract.text").alias("abstract_arr"),
            col("body_text.text").alias("body_text_arr"),
            col("back_matter.text").alias("back_matter_arr"),
            #col("metadata.authors").alias("authors_arr"),
            "paper_id")

# concatenate the paragraphs in one text for abstartc, body_text and back_matter
noncomm_use_subset_selected = noncomm_use_subset_selected.withColumn('abstract', concat_ws(', ', 'abstract_arr'))
noncomm_use_subset_selected = noncomm_use_subset_selected.withColumn('body_text', concat_ws(', ', 'body_text_arr'))
noncomm_use_subset_selected = noncomm_use_subset_selected.withColumn('back_matter', concat_ws(', ', 'back_matter_arr'))

# add column for source dataset
noncomm_use_subset_selected = noncomm_use_subset_selected.withColumn("source",lit("noncomm_use_subset"))

# drop unneeded columns 
noncomm_use_subset_selected = noncomm_use_subset_selected.drop("abstract_arr","body_text_arr","back_matter_arr")

noncomm_use_subset_selected.printSchema()

root
-- title: string (nullable = true)
-- paper_id: string (nullable = true)
-- abstract: string (nullable = false)
-- body_text: string (nullable = false)
-- back_matter: string (nullable = false)
-- source: string (nullable = false)

In [0]:
# select columns which have text like title, abstract, body and backmatter
# select author object to make some processing later
# select paperid
biorxiv_medrxiv_selected = biorxiv_medrxiv.select(
            col("metadata.title").alias("title"),
            col("abstract.text").alias("abstract_arr"),
            col("body_text.text").alias("body_text_arr"),
            col("back_matter.text").alias("back_matter_arr"),
             # col("metadata.authors").alias("authors_arr"),
            "paper_id")

# concatenate the paragraphs in one text for abstartc, body_text and back_matter
biorxiv_medrxiv_selected = biorxiv_medrxiv_selected.withColumn('abstract', concat_ws(', ', 'abstract_arr'))
biorxiv_medrxiv_selected = biorxiv_medrxiv_selected.withColumn('body_text', concat_ws(', ', 'body_text_arr'))
biorxiv_medrxiv_selected = biorxiv_medrxiv_selected.withColumn('back_matter', concat_ws(', ', 'back_matter_arr'))

# add column for source dataset
biorxiv_medrxiv_selected = biorxiv_medrxiv_selected.withColumn("source",lit("biorxiv_medrxiv"))

# drop unneeded columns 
biorxiv_medrxiv_selected = biorxiv_medrxiv_selected.drop("abstract_arr","body_text_arr","back_matter_arr")

biorxiv_medrxiv_selected.printSchema()


root
-- title: string (nullable = true)
-- paper_id: string (nullable = true)
-- abstract: string (nullable = false)
-- body_text: string (nullable = false)
-- back_matter: string (nullable = false)
-- source: string (nullable = false)

In [0]:
# Concatenate all datasets in one dataframe (comm_use_subset_selected, noncomm_use_subset_selected, biorxiv_medrxiv_selected)
# after selecting the neeeded columsn only
all_data_df = comm_use_subset_selected.union(noncomm_use_subset_selected).union(biorxiv_medrxiv_selected)
all_data_df.printSchema()

root
-- title: string (nullable = true)
-- paper_id: string (nullable = true)
-- abstract: string (nullable = false)
-- body_text: string (nullable = false)
-- back_matter: string (nullable = false)
-- source: string (nullable = false)

In [0]:
# get the counts for each group of records
from pyspark.sql.functions import count, countDistinct
display(all_data_df.groupBy("source").agg(count("paper_id")))

source count(paper_id) biorxiv_medrxiv 803 comm_use_subset 8997 noncomm_use_subset 1972

In [0]:
from pyspark.sql.functions import length
from pyspark.sql.functions import regexp_replace, col

# check number of null titles
print("Number of null titles:  ", all_data_df.select("title").where(col("title").isNull()).count())

# check the values of title which has columns empty
count_titles = all_data_df.select("title").where(col("title") == "").count()
print("Number of empty titles: ", count_titles)

Number of null titles: 0
Number of empty titles: 617

In [0]:
# check number of null abstratcs
print("Number of null abstracts:  ", all_data_df.select("abstract").where(col("abstract").isNull()).count())

# check the values of abstract which has columns less than 100 charcters which is so small
count_abstratcs = all_data_df.select("abstract").where(length(col("abstract")) < 100 ).count()
print("Number of abstracts has less than 100 char: ", count_abstratcs)

# check the values of abstract which has columns less than 100 charcters and not empty
count_abstratcs2 = all_data_df.select("abstract").where(length(col("abstract")) < 100 ).where(col("abstract") != "" ).count()
print("Number of abstracts has less than 100 char and not empty: ", count_abstratcs2)

Number of null abstracts: 0
Number of abstracts has less than 100 char: 1624
Number of abstracts has less than 100 char and not empty: 107

In [0]:
#display the abstratcs which is not empty and has less than 100 char
display(all_data_df.select("abstract").where(length(col("abstract")) < 100 ).where(col("abstract") != "" ))

abstract Mallard ducks are PLOS ONE | As globalization increases the interconnectedness between nations, economies, and industries, The diagnosis of rabies is routinely based on Melioidosis is a Background The emergence of Zika virus (ZIKV) Exposure of neonates to Mycobacterium avium subsp. School children may transmit pathogens with cluster cases occurring on campuses and in families. Objective: Human pluripotent stem cells are self-renewing cells with the ability to dif OPEN ACCESS PLOS ONE | In 2014 the World Viral respiratory and intestinal infections are the most common causes of canine viral illness. PLOS ONE | https://doi. Bundesgesundheitsbl 2020 · 63:65-73 https://doi. Published: xx xx xxxx OPEN www.nature.com/scientificreports/ 2 Scientific RepoRts | 7: 660 | PLOS ONE | Introduction Paleovirology is the study of ancient viruses. Perspectives Global atlas of zoonotic viruses Dennis Carroll et al. Diseases in introduced broilers can possibly spill over to wild birds on the Galapagos. Endemic and seasonally recurring respiratory viruses are a Here we present technical and mathematical results supporting the main paper. Cystic fibrosis ( There has been a dramatic increase in the number of insect-specific flaviviruses (ISFs) In addition to protective " Throughout the process of pathogen-host co- Elena Carnero and Marina Barriocanal have contributed equally to this work. The rapid emergence of AIDS in humans during the period between Victor M Corman et al. The objective of this study was to evaluate the effectiveness of the SurePure PLOS ONE | PLOS ONE | Negative staining electron microscopy methods can Viral pathogens cause devastating economic losses in poultry industries worldwide. Subject Areas: health and disease and epidemiology, computational biology The emergence of severe acute respiratory syndrome (SARS) Essays articulate a specific perspective on a topic of broad interest to scientists. Phyllostomid bat microbiome composition is associated to host phylogeny and feeding strategies Background: Surveillance and intervention are resource- The genome of HAdV-B14p1 strain BJ430 In December 2019 Drak2 is a serine/threonine kinase expressed highest in T cells and B cells. Published: xx xx xxxx OPEN www.nature.com/scientificreports/ 2 ScIentIfIc REpoRTS | (2018) 8:4801 | Citation details: Chen,L., Liu,B., Yang,J. et al. DBatVir: the database of bat-associated viruses. Interspecies transmission of pathogens may The emergence of the Middle To examine the impacts of a multi- Background: With sequencing technologies becoming cheaper and easier to use, Background: A rapid rise in PubMed citations on methicillin-resistant OPEN ACCESS Subject Areas: health and disease and epidemiology, computational biology When a pathogen is rare From . Analytical and spectral data of PQ-CAD amides 3a-k. 65 -72-74 following order: 1. Supplementary Figures and Legends. 2. Supplementary references. We surely need WHO more than ever. Kirchdoerfer et al. These authors contributed equally to this work. A number of virologic and A demyelinating disease induced in Dr. Friedrich's current address is Brookdale The ␣ 2,3 sialyltransferase, ␣ 2,3 SAT (O), Oligonucleotide-directed mutagenesis was PLATES 45 ~o 50 To cite: Rabinowitz PMacG, Pappaioanou M, Bardosh KL, et al. A planetary vision for one health. Background: Cruise ships carry a large number of people in confined spaces with relative Middle east respiratory syndrome coronavirus. N Engl J Med. 2013; 369:407-16., ReFeRenCes † These authors contributed equally to this work www.pnas.org/cgi/ 19 Members of the rab/YPTI/SEC4 gene family The intracellular transport of newly synthe- The type H membrane protein p63 is a resi- The mechanism by which yeast dipeptidyl aminopeptidase (DPAP) A, a type II integral mem- Yeast Sec12p is a type II transmembrane Epithelial cells accumulate distinct popula- The localization of proteins to late-Golgi Brefeldin A (BFA) was shown in earlier studies of numerous cell ty

In [0]:
# check number of null body_text
print("Number of null body_text:  ", all_data_df.select("body_text").where(col("body_text").isNull()).count())

# check the values of body_text which has columns less than 100 charcters which is so small
count_body_text = all_data_df.select("body_text").where(length(col("body_text")) < 10000 ).count()
print("Number of body_text has less than 10000 char: ", count_body_text)

# check the values of body_text which has columns less than 10000 charcters and not empty
count_body_text2 = all_data_df.select("body_text").where(length(col("body_text")) < 10000 ).where(col("body_text") != "" ).count()
print("Number of body_text has less than 10000 char and not empty: ", count_body_text2)

Number of null body_text: 0
Number of body_text has less than 10000 char: 1188
Number of body_text has less than 10000 char and not empty: 1188

In [0]:
#display the body_text which is not empty and has less than 100 char
display(all_data_df.select("body_text").where(length(col("body_text")) < 10000 ).where(col("body_text") != "" ))

body_text through oligonucleotide microarray analysis. J Vasc Surg 39: (3) 645. Kang D, Nam H, Kim YS, Moon MH. 2005 . Dual-purpose sample trap for on-line strong cation-exchange chromatography reversed-phase liquid chromatography tandem mass spectrometry for shotgun proteomics -Application to the human Jurkat T-cell proteome. J Chromatogr A 1070: (1-2) 193. Kannangai R, Diehl AM, Sicklick J, Rojkind M, Thomas D, Torbenson M. 2005 . Hepatic angiomyolipoma and hepatic stellate cells share a similar gene expression profile. Hum Pathol 36: (4) 341. Kano M, Tsutsumi S, Kawahara N, Wang Y, Mukasa A, Kirino T, Aburatani H. 2005 . A meta-clustering analysis indicates distinct pattern alteration between two series of gene expression profiles for induced ischemic tolerance in rats. Physiol Genomics 21: (2) 274. Karlsson H, Leanderson P, Tagesson C, Lindahl M. 2005. Lipoproteomics II: Mapping of proteins in high-density lipoprotein using two-dimensional gel electrophoresis and mass spectrometry. 2005. Genetic expression profiles during physiological and pathological cardiac hypertrophy and heart failure in rats. Physiol Genomics 21: (1) 34. Kume E, Aruga C, Ishizuka Y, Takahashi Lu CD, Yang Z, Li W. 2004 2004. Proteomic analysis of differential protein expression in a human hepatoma revertant cell line by using an improved two-dimensional electrophoresis procedure combined with matrix assisted laser desorption/ionization-time of flight-mass spectrometry. Supplementary Table 1 J/A- [191] Pigs GII.11 GII. 11 9 Norway rat (Rattus norvegicus) 16 10 Yellow necked mouse (Apodemus flavicollis) 11 Could not be sequenced 12 Collected from untouched fresh snow 13 Rhesus/Pigtail/cynomologus Xanthomonas campestris JX, sequence accession AJVO00000000 [75] Yersinia pestis Strain 2501, sequence accession AKVQ00000000 [76] Phylum Firmicutes "Geobacillus thermoglucosidans" TNO-09.020, sequence accession AJJN00000000 [93] Aerococcus viridans LL1, sequence accession AJTG00000000 [78] Bacillus anthracis H9401, sequence accession CP002091.1 ( chromosome), CP002092.1.1 (plasmid pXO1), and CP002093.1 (plasmid pXO2) [79] Bacillus atrophaeus C89, sequence accession AJRJ00000000 [80] Bacillus cereus NC7401, sequence accession AP007209 (chromosome), AP007210 (plasmid pNCcld), AP007211 (plasmid pNC1, 48 kb), AP007212 (plasmid pNC2, 5 kb), AP007213 (plasmid pNC3, 4 kb), and AP007214 (plasmid pNC4, 3 kb) [81] Bacillus methanolicus MGA3, sequence accession ADWW00000000 [82] Bacillus methanolicus PB1, sequence accession AFEU00000000 [82] Bacillus siamensis KCTC 13613 T , sequence accession AJVF00000000 [83] Bacillus sp. Strain 5B6, sequence accession AJST00000000 [84] Bacillus sp. Strain 916, sequence accession AFSU00000000 [85] Clostridium beijerinckii Strain G117, sequence acceession AKWA00000000 [87] Corynebacterium pseudotuberculosis Strain 1/06-A, sequence accession CP003082 [88] Enterococcus faecalis D32, sequence accession CP003726 through CP003728 [90] Enterococcus faecalis strain NP-10011, sequence accession AB712291 [91] Enterococcus faecium Clinical Isolate LCT-EF128, sequence accession AJUP00000000 [27] Enterococcus hirae (Streptococcus faecalis) ATCC 9790, sequence accession CP003504 (chromosome), NC_015845 (plasmid pTG9790) [92] Streptococcus thermophilus Strain MN-ZLW-002, sequence accession CP003499 [113] Ureibacillus thermosphaericus Strain Thermo-BF, sequence accession AJIK00000000 [114] Phylum Tenericutes Mycoplasma leachii Strain PG50 T , sequence accession CP002108.1 [115] Mycoplasma mycoides subsp. mycoides, sequence accession CP002107.1 [115] Mycoplasma wenyonii Strain Massachusetts, sequence accession CP003703 [116] Phylum Actinobacteria Actinomyces massiliensis Strain 4401292 T , sequence accession AKIO00000000 [117] Bifidobacterium animalis subsp. lactis B420, sequence accesion CP003497 [118] Bifidobacterium animalis subsp. lactis Bi-07, sequence accesion CP003498 [118] Bifidobacterium bifidum strain BGN4, sequence accession CP001361 [119] Br

In [0]:
#display the body_text which is not empty and has less than 1000 char for one record
print(all_data_df.select("body_text").where(length(col("body_text")) < 10000 ).where(col("body_text") != "" ).collect()[0][0])

Out[53]: 'through oligonucleotide microarray analysis. J Vasc Surg 39: (3) 645. Kang D, Nam H, Kim YS, Moon MH. 2005 . Dual-purpose sample trap for on-line strong cation-exchange chromatography reversed-phase liquid chromatography tandem mass spectrometry for shotgun proteomics -Application to the human Jurkat T-cell proteome. J Chromatogr A 1070: (1-2) 193. Kannangai R, Diehl AM, Sicklick J, Rojkind M, Thomas D, Torbenson M. 2005 . Hepatic angiomyolipoma and hepatic stellate cells share a similar gene expression profile. Hum Pathol 36: (4) 341. Kano M, Tsutsumi S, Kawahara N, Wang Y, Mukasa A, Kirino T, Aburatani H. 2005 . A meta-clustering analysis indicates distinct pattern alteration between two series of gene expression profiles for induced ischemic tolerance in rats. Physiol Genomics 21: (2) 274. Karlsson H, Leanderson P, Tagesson C, Lindahl M. 2005. Lipoproteomics II: Mapping of proteins in high-density lipoprotein using two-dimensional gel electrophoresis and mass spectrometry. 2005. Genetic expression profiles during physiological and pathological cardiac hypertrophy and heart failure in rats. Physiol Genomics 21: (1) 34. Kume E, Aruga C, Ishizuka Y, Takahashi '

In [0]:
# check number of null back_matter
print("Number of null back_matter:  ", all_data_df.select("back_matter").where(col("back_matter").isNull()).count())

# check the values of back_matter which has columns less than 100 charcters which is so small
count_back_matter = all_data_df.select("back_matter").where(length(col("back_matter")) < 100 ).count()
print("Number of back_matter has less than 100 char: ", count_back_matter)

# check the values of back_matter which has columns less than 100 charcters and not empty
count_back_matter2 = all_data_df.select("back_matter").where(length(col("back_matter")) < 100 ).where(col("back_matter") != "" ).count()
print("Number of back_matter has less than 100 char and not empty: ", count_back_matter2)


Number of null back_matter: 0
Number of back_matter has less than 100 char: 3776
Number of back_matter has less than 100 char and not empty: 974

In [0]:
#display the back_matter which is not empty and has less than 100 char
display(all_data_df.select("back_matter").where(length(col("back_matter")) < 100 ).where(col("back_matter") != "" ))

back_matter Ayele M, Haas BJ, Kumar N, Wu H The authors declare no conflict of interest. The authors declare no conflict of interest. The authors declare no conflict of interest. The authors declare no conflicts of interest. We apologise to those authors whose work was not cited directly owing to space limitations. We These studies were supported by the Russian Science Foundation (Grant 16-15-00199). The authors declare no conflict of interest. This work was supported by Science and Technology Development Acknowledgments This work has been in part supported by grants-in- The authors declare no conflict of interest. This work was supported by the grant from the National Natural Science Foundation of The authors declare no conflict of interest. Submit your next manuscript to BioMed Central and take full advantage of: The authors declare that there is no conflict of interests regarding the publication of this paper. The authors declare no conflict of interest. The authors declare no conflicts of interest. The authors declare no conflict of interest. We thank our team for support and scientific input. We would like to thank Allison Black for useful discussion and advice. GD We thank Paul Masters for providing anti-I sera. The authors wish to acknowledge Dr. Catherine Gangell for reviewing the manuscript. The authors declare that the research was The authors declare no conflict of interest. We are grateful to Yongxin Yu (National Institutes for Food and Drug Control) for the The authors would like to acknowledge Fundação para a Ciência e a Tecnologia, Portugal, The authors declare no conflict of interest. I would like to thank all the reviewers for their constructive suggestions and comments. The authors have no conflict of interest to declare. Funding: No external funding was received. The author declares no conflict of interest. The authors declare no conflict of interest. Funding: This research received no external funding. The authors declare no conflict of interest. The authors declare no conflict of interest.Viruses 2016, 8, 154 Submit your next manuscript to BioMed Central and take full advantage of: The authors declare no conflict of interest. We thank Dr. Dennis Kolson for discussion and reading the manuscript. We are grateful to C. Galanos, S. Tchapchet, P. Nielsen and I. Gyory The authors declare no conflict of interest. We thank Katherine Van for helpful discussions. The authors declare no conflict of interest. This work was supported by grants from AHA (13POST17210033) and NSFC (81101553) to Dr. Zhong. The authors declare no conflict of interest. We thank Hans Günter Bredow, ZBS 4, RKI for his patient IT-editing of the Figures, the staff Funding: This work supported by the Mayo Foundation. The author declares no conflicts of interest. The authors declare no conflict of interest. We would like to thank Kelly Coller and Nicholas Heaton for critical reading of the manuscript. We thank Marga Gonzalez for technical assistance. We thank Dr. Marijke Keestra The authors declare no conflict of interest. The authors declare no conflicts of interest. We thank Ursula Erikli for copyediting. The authors declare no conflict of interest. This work is supported by NIH Grant HL081420. All data generated during this study are included in the manuscript and supporting files. We kindly acknowledge the gift of reagents from Dr. Motohiro Tani Submit your next manuscript to BioMed Central and take full advantage of: The authors declare no conflict of interest. We thank Vinod Kumar for his assistance in computational analysis. The authors declare no conflict of interest.Viruses 2019, 11, 210 The authors declare no conflict of interest. The authors declare no conflict of interest. We thank Beth Groom for helpful discussion on the manuscript. The authors declare no conflict of interest. We The authors declare no conflict of interest. There is no conflict of interest. We thank the SAM Vaccine Platform Team at GSK Vaccines, and in particular, P. 

In [0]:
"""After exploring the data we found 3 options:
      1. Use title to be features
      2. Use abstract to be features
      3. Use body_text to be features
      4. merge abstract and body_text
      
   So we try all of them and unfortunaty there is no big difference between options in the clustreing results
"""

In [0]:
from pyspark.sql.functions import concat, coalesce  
all_data_df = all_data_df.withColumn("all_text", concat(coalesce(col("abstract")), coalesce(col("body_text"))))

In [0]:
from pyspark.sql.functions import length
all_data_df = all_data_df.where(col("title") != "" ).where(length(col("title")) > 50 )

In [0]:
print("total count of records: ", all_data_df.count())
print("total count of unique titles: ", all_data_df.select("title").distinct().count())

#remove duplicate title records 
all_data_df = all_data_df.dropDuplicates(["title"])
print("total count of records after remove duplicate: ", all_data_df.count())

total count of records: 10441
total count of unique titles: 10389
total count of records after remove duplicate: 10389

In [0]:
from langdetect import detect
from pyspark.sql.types import StringType
from pyspark.sql.functions import udf

def language_detect(data_str):
    lang = detect(data_str) 
    return lang

language_detect_udf = udf(language_detect, StringType())
all_data_df = all_data_df.withColumn('language', language_detect_udf(all_data_df.title))
all_data_df.printSchema()

root
-- title: string (nullable = true)
-- paper_id: string (nullable = true)
-- abstract: string (nullable = false)
-- body_text: string (nullable = false)
-- back_matter: string (nullable = false)
-- source: string (nullable = false)
-- all_text: string (nullable = false)
-- language: string (nullable = true)

In [0]:
print("total count of records: ", all_data_df.count())
print("total count of non English records: ", all_data_df.where(col("language") != 'en').count())

#remove non English records 
all_data_df = all_data_df.where(col("language") == 'en')
print("total count of English records only: ", all_data_df.count())

total count of records: 10389
total count of non English records: 96
total count of English records only: 10292

In [0]:
from pyspark.ml.feature import RegexTokenizer

regexTokenizer = RegexTokenizer(gaps = False, pattern = '\w+', inputCol = 'title', outputCol = 'text_token')

all_data_df_token = regexTokenizer.transform(all_data_df)
all_data_df_token.select("paper_id", "title", "text_token").show(3)

+--------------------+--------------------+--------------------+
 paper_id| title| text_token|
+--------------------+--------------------+--------------------+
6bdb41aa63efed506...|A Simple Method t...|[a, simple, metho...|
765003fdad3ad535f...|A Simplified Posi...|[a, simplified, p...|
3c14c4c3a176c8683...|A comprehensive a...|[a, comprehensive...|
+--------------------+--------------------+--------------------+
only showing top 3 rows

In [0]:
display(all_data_df_token.select("title", "text_token"))

In [0]:
from pyspark.ml.feature import StopWordsRemover
swr = StopWordsRemover(inputCol = 'text_token', outputCol = 'text_sw_removed')
print(swr.getStopWords())
all_data_df_sw = swr.transform(all_data_df_token)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', 'her', 'hers', 'herself', 'it', 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', 'too', 'very', 's', 't', 'can', 'will', 'just', 'don', 'should', 'now', "i'll", "you'll", "he'll", "she'll", "we'll", "they'll", "i'd", "you'd", "he'd", "she'd", "we'd", "they'd", "i'm", "you're", "he's", "she's", "it's", "we're", "they're", "i've", "we've", "you've", "they've", "isn't", "aren't", "wasn't", "weren't", "haven't", "hasn't", "hadn't", "don't", "doesn't", "didn't", "won't", "wouldn't", "shan't", "shouldn't", "mustn't", "can't", "couldn't", 'cannot', 'could', "here's", "how's", "let's", 'ought', "that's", "there's", "what's", "when's", "where's", "who's", "why's", 'would']

In [0]:
custom_stop_words = ['doi', 'preprint', 'copyright', 'peer', 'reviewed', 'org',
'https', 'et', 'al', 'author', 'figure','rights', 'reserved', 'permission', 'used', 'using',
'biorxiv', 'medrxiv', 'license', 'fig', 'fig.', 'al.', 'Elsevier', 'PMC', 'CZI', 'www']

cswr = StopWordsRemover(inputCol = 'text_sw_removed', outputCol = 'text_csp_removed')
cswr.setStopWords(custom_stop_words)
print(cswr.getStopWords())
all_data_df_sw = cswr.transform(all_data_df_sw)
all_data_df_sw.select("paper_id", "title", "text_token","text_sw_removed","text_csp_removed").show(3)

['doi', 'preprint', 'copyright', 'peer', 'reviewed', 'org', 'https', 'et', 'al', 'author', 'figure', 'rights', 'reserved', 'permission', 'used', 'using', 'biorxiv', 'medrxiv', 'license', 'fig', 'fig.', 'al.', 'Elsevier', 'PMC', 'CZI', 'www']
+--------------------+--------------------+--------------------+--------------------+--------------------+
 paper_id| title| text_token| text_sw_removed| text_csp_removed|
+--------------------+--------------------+--------------------+--------------------+--------------------+
6bdb41aa63efed506...|A Simple Method t...|[a, simple, metho...|[simple, method, ...|[simple, method, ...|
765003fdad3ad535f...|A Simplified Posi...|[a, simplified, p...|[simplified, posi...|[simplified, posi...|
3c14c4c3a176c8683...|A comprehensive a...|[a, comprehensive...|[comprehensive, a...|[comprehensive, a...|
+--------------------+--------------------+--------------------+--------------------+--------------------+
only showing top 3 rows

In [0]:
display(all_data_df_sw.select("title", "text_token","text_csp_removed"))

In [0]:
#TF-IDF. This will convert our string formatted data into a measure of how important
#each word is to the instance out of the record as a whole.

from pyspark.ml.feature import HashingTF
#65535
hashingTF = HashingTF(inputCol="text_csp_removed", outputCol="rawFeatures", numFeatures=250)
all_data_df_rawFeatures = hashingTF.transform(all_data_df_sw)
#all_data_df_rawFeatures.select("paper_id","text_csp_removed", "rawFeatures").show(3)

In [0]:
from pyspark.ml.feature import IDF
idf = IDF(inputCol="rawFeatures", outputCol="features", minDocFreq=5)
all_data_df_features = idf.fit(all_data_df_rawFeatures).transform(all_data_df_rawFeatures)
#all_data_df_features.select("paper_id","text_csp_removed", "rawFeatures", "features").show(5)

In [0]:
from pyspark.ml.feature import  PCA
pca = PCA(k=3, inputCol="features", outputCol="pcaFeatures")
all_data_df_features_pca = pca.fit(all_data_df_features)

In [0]:
all_data_df_features_pca = all_data_df_features_pca.transform(all_data_df_features)
all_data_df_features_pca.select("paper_id", "features", "pcaFeatures").show(3)

+--------------------+--------------------+--------------------+
 paper_id| features| pcaFeatures|
+--------------------+--------------------+--------------------+
6bdb41aa63efed506...|(250,[31,40,65,72...|[-0.8059698724145...|
765003fdad3ad535f...|(250,[1,5,46,94,9...|[-1.1412955825137...|
3c14c4c3a176c8683...|(250,[10,44,46,54...|[-1.1464510652878...|
+--------------------+--------------------+--------------------+
only showing top 3 rows

In [0]:
# ----- inprogress ------
import numpy as np
cost = np.zeros(20)
for k in range(2,20):
    kmeans = KMeans()\
            .setK(k)\
            .setSeed(1) \
            .setFeaturesCol("pcaFeatures")\
            .setPredictionCol("cluster")

    model = kmeans.fit(all_data_df_features_pca)
    cost[k] = model.computeCost(all_data_df_features_pca)
    print("k: " , k," ", cost[k])

k: 2 34615.19784787532
k: 3 27173.366485608334
k: 4 26672.423127914313

In [0]:
import numpy as np
import matplotlib.mlab as mlab
import matplotlib.pyplot as plt
import seaborn as sbs
from matplotlib.ticker import MaxNLocator

fig, ax = plt.subplots(1,1, figsize =(8,6))
ax.plot(range(2,20),cost[2:20])
ax.set_xlabel('k')
ax.set_ylabel('cost')
ax.xaxis.set_major_locator(MaxNLocator(integer=True))
plt.show()

In [0]:
from pyspark.ml.clustering import KMeans

# Loads data.
dataset = all_data_df_features_pca.select("pcaFeatures")

# Trains a k-means model.
kmeans = KMeans().setK(3).setFeaturesCol("pcaFeatures")
model = kmeans.fit(dataset)

# Make predictions
predictions = model.transform(dataset)

In [0]:
from pyspark.ml.evaluation import ClusteringEvaluator

# Evaluate clustering by computing Silhouette score
evaluator = ClusteringEvaluator().setFeaturesCol("pcaFeatures")

silhouette = evaluator.evaluate(predictions)
print("Silhouette with squared euclidean distance = " + str(silhouette))

Silhouette with squared euclidean distance = 0.4736138751540979

In [0]:
display(predictions.groupBy("prediction").count()) 

prediction count 1 7077 2 1088 0 2132

In [0]:
from pyspark.ml import Pipeline
pipeline = Pipeline(stages=[regexTokenizer, swr,cswr, hashingTF, idf,pca, kmeans])

model = pipeline.fit(all_data_df)
results = model.transform(all_data_df)

display(results.groupBy("prediction").count()) 

prediction count 1 8878 2 3 0 1414